In [1]:
import pandas as pd
from orangecontrib.associate.fpgrowth import *  
import Orange

C:\Users\James\Anaconda3\lib\site-packages\h5py\__init__.py:36: FutureWarning: Conversion of the second argument of issubdtype from `float` to `np.floating` is deprecated. In future, it will be treated as `np.float64 == np.dtype(float).type`.
  from ._conv import register_converters as _register_converters


In [2]:

movies = pd.read_table('movies.dat')



In [3]:
movies = movies[(movies['movieID']<50)]

In [4]:


movieNames = pd.read_table('movieNames.dat')


In [5]:



viewed = dict()
for row in movies.itertuples():
    if row[1] not in viewed:
        
        viewed[row[1]] = list(movieNames[movieNames['id']==row[2]]['title'])[0]
    else:
        viewed[row[1]] += ', '
        viewed[row[1]] += list(movieNames[movieNames['id']==row[2]]['title'])[0]



In [6]:

raw_data = list(viewed.values())

f = open('movieData.basket', 'w', encoding='utf-8')
for item in raw_data:
    f.write(item + '\n')
f.close()


In [7]:
data = Orange.data.Table("movieData.basket")
X, mapping = OneHot.encode(data, include_class=True)



In [8]:
itemsets = dict(frequent_itemsets(X, .15))

In [9]:
class_items ={item for item, var, _ in OneHot.decode(mapping, data, mapping)}

In [11]:
rules = [(P, Q, supp/len(X), conf) for P, Q, supp, conf in association_rules(itemsets,min_confidence = 0.4) if len(Q) == 1 and Q & class_items]

In [12]:
names = {item: '{}'.format(var.name) for item, var, val in OneHot.decode(mapping, data, mapping)}


{0: 'Grumpy Old Men',
 1: 'Twelve Monkeys',
 2: 'Sense and Sensibility',
 3: 'La cité des enfants perdus',
 4: 'Richard III',
 5: 'Toy story',
 6: 'Jumanji',
 7: 'GoldenEye',
 8: 'Ace Ventura: When Nature Calls',
 9: 'Get Shorty',
 10: 'Babe',
 11: 'Clueless',
 12: 'Shichinin no samurai',
 13: 'Heat',
 14: 'Leaving Las Vegas',
 15: 'Dead Man Walking',
 16: 'Sabrina',
 17: 'Pocahontas',
 18: 'Father of the Bride Part II',
 19: 'The American President',
 20: 'Casino',
 21: 'Four Rooms',
 22: 'Money Train',
 23: 'Copycat',
 24: 'Now and Then',
 25: 'Dangerous Minds',
 26: 'Live Free or Die Hard',
 27: 'How to Make an American Quilt',
 28: 'Othello',
 29: 'Sudden Death',
 30: 'Dead Presidents',
 31: 'Balto',
 32: 'Mortal Kombat',
 33: 'Dracula: Dead and Loving It',
 34: 'Cutthroat Island',
 35: 'Persuasion',
 36: 'Restoration',
 37: 'Ninja Assassin',
 38: 'Powder',
 39: 'Yao a yao yao dao waipo qiao',
 40: 'Carrington',
 41: 'Nixon',
 42: 'Waiting to Exhale',
 43: 'Cry',
 44: 'the Beloved 

In [13]:
print('Association Rules:')
for ante, cons, supp, conf in rules:
    print(', '.join(names[i] for i in ante), '-->', names[next(iter(cons))],
    '(supp: {:0.2f}, conf: {:0.2f})'.format(supp, conf))

Association Rules:
Babe, Shichinin no samurai, Toy story, Jumanji --> Twelve Monkeys (supp: 0.15, conf: 0.85)
Twelve Monkeys, Babe, Shichinin no samurai, Jumanji --> Toy story (supp: 0.15, conf: 0.93)
Twelve Monkeys, Babe, Shichinin no samurai, Toy story --> Jumanji (supp: 0.15, conf: 0.69)
Twelve Monkeys, Shichinin no samurai, Toy story, Jumanji --> Babe (supp: 0.15, conf: 0.69)
Twelve Monkeys, Babe, Toy story, Jumanji --> Shichinin no samurai (supp: 0.15, conf: 0.88)
Shichinin no samurai, Toy story, Jumanji, GoldenEye --> Twelve Monkeys (supp: 0.15, conf: 0.87)
Twelve Monkeys, Shichinin no samurai, Jumanji, GoldenEye --> Toy story (supp: 0.15, conf: 0.91)
Twelve Monkeys, Shichinin no samurai, Toy story, GoldenEye --> Jumanji (supp: 0.15, conf: 0.69)
Twelve Monkeys, Shichinin no samurai, Toy story, Jumanji --> GoldenEye (supp: 0.15, conf: 0.70)
Twelve Monkeys, Toy story, Jumanji, GoldenEye --> Shichinin no samurai (supp: 0.15, conf: 0.92)
Ace Ventura: When Nature Calls, Shichinin no s

In [23]:
userNum = 0
for user in X:
    print('\n\nUser {}'.format(userNum))
    print('Movies Seen:\n{}'.format(', '.join(names[i] for i in user)))
    print('\nPossible Recommendations:')
    recommendations = dict()
    for rule in rules:
        if list(rule[1])[0] not in user:
            if rule[0].issubset(user):
                    ante, cons, supp, conf = rule
                    if names[list(cons)[0]] not in recommendations:
                        recommendations[names[list(cons)[0]]] = 1
                    else:
                        recommendations[names[list(cons)[0]]] += 1
                    print(', '.join(names[i] for i in ante), '-->', names[next(iter(cons))],
                          '(supp: {:0.2f}, conf: {:0.2f})'.format(supp, conf))
    print('\nFrequency of Recommendations:')
    print(recommendations)
        
    
    userNum += 1



User 0
Movies Seen:
Grumpy Old Men, Twelve Monkeys

Possible Recommendations:
Twelve Monkeys --> Shichinin no samurai (supp: 0.48, conf: 0.80)
Twelve Monkeys --> Toy story (supp: 0.44, conf: 0.72)
Twelve Monkeys --> Babe (supp: 0.28, conf: 0.47)
Twelve Monkeys --> Jumanji (supp: 0.29, conf: 0.48)
Twelve Monkeys --> GoldenEye (supp: 0.29, conf: 0.48)
Twelve Monkeys --> Ace Ventura: When Nature Calls (supp: 0.27, conf: 0.44)
Twelve Monkeys --> Clueless (supp: 0.25, conf: 0.41)
Twelve Monkeys --> Heat (supp: 0.26, conf: 0.42)

Frequency of Recommendations:
{'Shichinin no samurai': 1, 'Toy story': 1, 'Babe': 1, 'Jumanji': 1, 'GoldenEye': 1, 'Ace Ventura: When Nature Calls': 1, 'Clueless': 1, 'Heat': 1}


User 1
Movies Seen:
Twelve Monkeys, Sense and Sensibility, La cité des enfants perdus, Richard III

Possible Recommendations:
Twelve Monkeys --> Shichinin no samurai (supp: 0.48, conf: 0.80)
Twelve Monkeys --> Toy story (supp: 0.44, conf: 0.72)
Twelve Monkeys --> Babe (supp: 0.28, conf: 

Ace Ventura: When Nature Calls --> Clueless (supp: 0.19, conf: 0.51)
Babe --> Clueless (supp: 0.21, conf: 0.53)
GoldenEye --> Casino (supp: 0.16, conf: 0.41)
Heat --> Casino (supp: 0.17, conf: 0.56)
Get Shorty --> Clueless (supp: 0.16, conf: 0.60)

Frequency of Recommendations:
{'Clueless': 25, 'Casino': 7}


User 21
Movies Seen:
Twelve Monkeys, Toy story, Jumanji, GoldenEye, Ace Ventura: When Nature Calls, Babe, Shichinin no samurai, Pocahontas, Four Rooms, Dangerous Minds

Possible Recommendations:
Twelve Monkeys, Shichinin no samurai, Toy story --> Clueless (supp: 0.19, conf: 0.51)
Shichinin no samurai, Toy story, Jumanji --> Clueless (supp: 0.15, conf: 0.59)
Babe, Shichinin no samurai, Toy story --> Clueless (supp: 0.15, conf: 0.58)
Twelve Monkeys, Shichinin no samurai, Toy story --> Heat (supp: 0.19, conf: 0.52)
Twelve Monkeys, Shichinin no samurai, GoldenEye --> Heat (supp: 0.16, conf: 0.62)
Shichinin no samurai, Toy story, GoldenEye --> Heat (supp: 0.15, conf: 0.60)
Twelve Monke

Twelve Monkeys, GoldenEye --> Ace Ventura: When Nature Calls (supp: 0.17, conf: 0.59)
Toy story, GoldenEye --> Ace Ventura: When Nature Calls (supp: 0.19, conf: 0.61)
Twelve Monkeys, Shichinin no samurai --> Ace Ventura: When Nature Calls (supp: 0.23, conf: 0.48)
Shichinin no samurai, Toy story --> Ace Ventura: When Nature Calls (supp: 0.24, conf: 0.52)
Shichinin no samurai, GoldenEye --> Ace Ventura: When Nature Calls (supp: 0.18, conf: 0.61)
Twelve Monkeys, Toy story --> Clueless (supp: 0.21, conf: 0.49)
Twelve Monkeys, GoldenEye --> Clueless (supp: 0.15, conf: 0.52)
Toy story, GoldenEye --> Clueless (supp: 0.17, conf: 0.53)
Twelve Monkeys, Shichinin no samurai --> Clueless (supp: 0.21, conf: 0.44)
Shichinin no samurai, Toy story --> Clueless (supp: 0.22, conf: 0.48)
Shichinin no samurai, GoldenEye --> Clueless (supp: 0.15, conf: 0.50)
Twelve Monkeys, Heat --> Jumanji (supp: 0.15, conf: 0.59)
Shichinin no samurai, Heat --> Jumanji (supp: 0.16, conf: 0.58)
Twelve Monkeys, Toy story --

Twelve Monkeys, Toy story --> Babe (supp: 0.25, conf: 0.58)
Shichinin no samurai, Toy story --> Babe (supp: 0.26, conf: 0.57)
Twelve Monkeys, Shichinin no samurai --> Jumanji (supp: 0.25, conf: 0.52)
Twelve Monkeys, Toy story --> Jumanji (supp: 0.25, conf: 0.57)
Shichinin no samurai, Toy story --> Jumanji (supp: 0.26, conf: 0.57)
Twelve Monkeys, Toy story --> GoldenEye (supp: 0.25, conf: 0.57)
Twelve Monkeys, Shichinin no samurai --> GoldenEye (supp: 0.26, conf: 0.54)
Shichinin no samurai, Toy story --> GoldenEye (supp: 0.25, conf: 0.56)
Twelve Monkeys, Toy story --> Ace Ventura: When Nature Calls (supp: 0.22, conf: 0.51)
Twelve Monkeys, Shichinin no samurai --> Ace Ventura: When Nature Calls (supp: 0.23, conf: 0.48)
Shichinin no samurai, Toy story --> Ace Ventura: When Nature Calls (supp: 0.24, conf: 0.52)
Twelve Monkeys, Toy story --> Clueless (supp: 0.21, conf: 0.49)
Twelve Monkeys, Shichinin no samurai --> Clueless (supp: 0.21, conf: 0.44)
Shichinin no samurai, Toy story --> Cluele

Ace Ventura: When Nature Calls, Jumanji --> Babe (supp: 0.17, conf: 0.68)
Ace Ventura: When Nature Calls, Shichinin no samurai --> GoldenEye (supp: 0.18, conf: 0.65)
Ace Ventura: When Nature Calls, Shichinin no samurai --> Babe (supp: 0.17, conf: 0.60)
Twelve Monkeys, Clueless --> GoldenEye (supp: 0.15, conf: 0.62)
Clueless, Toy story --> GoldenEye (supp: 0.17, conf: 0.58)
Twelve Monkeys, Clueless --> Babe (supp: 0.16, conf: 0.65)
Clueless, Toy story --> Babe (supp: 0.19, conf: 0.68)
Clueless, Shichinin no samurai --> GoldenEye (supp: 0.15, conf: 0.60)
Clueless, Shichinin no samurai --> Babe (supp: 0.16, conf: 0.66)
Twelve Monkeys, Toy story --> Heat (supp: 0.20, conf: 0.46)
Twelve Monkeys, Jumanji --> Heat (supp: 0.15, conf: 0.52)
Twelve Monkeys, Shichinin no samurai --> Heat (supp: 0.24, conf: 0.49)
Shichinin no samurai, Toy story --> Heat (supp: 0.21, conf: 0.46)
Shichinin no samurai, Jumanji --> Heat (supp: 0.16, conf: 0.52)
Twelve Monkeys, Toy story --> Casino (supp: 0.18, conf: 0

...

Clueless, Shichinin no samurai, Toy story --> Jumanji (supp: 0.15, conf: 0.70)
Twelve Monkeys, Shichinin no samurai, Toy story --> Casino (supp: 0.17, conf: 0.45)
Twelve Monkeys, Shichinin no samurai, Toy story --> Get Shorty (supp: 0.16, conf: 0.43)
Twelve Monkeys, Babe --> Jumanji (supp: 0.18, conf: 0.65)
Twelve Monkeys, Shichinin no samurai --> Jumanji (supp: 0.25, conf: 0.52)
Babe, Shichinin no samurai --> Jumanji (supp: 0.19, conf: 0.65)
Twelve Monkeys, Toy story --> Jumanji (supp: 0.25, conf: 0.57)
Babe, Toy story --> Jumanji (supp: 0.22, conf: 0.64)
Shichinin no samurai, Toy story --> Jumanji (supp: 0.26, conf: 0.57)
Twelve Monkeys, GoldenEye --> Jumanji (supp: 0.18, conf: 0.63)
Toy story, GoldenEye --> Jumanji (supp: 0.20, conf: 0.65)
Babe, GoldenEye --> Jumanji (supp: 0.16, conf: 0.70)
Shichinin no samurai, GoldenEye --> Jumanji (supp: 0.19, conf: 0.64)
Ace Ventura: When Nature Calls, Twelve Monkeys --> Jumanji (supp: 0.19, conf: 0.70)
Ace Ventura: When Nature Calls, Toy story

Shichinin no samurai --> Heat (supp: 0.27, conf: 0.43)

Frequency of Recommendations:
{'Toy story': 1, 'Twelve Monkeys': 1, 'Babe': 1, 'Jumanji': 1, 'GoldenEye': 1, 'Ace Ventura: When Nature Calls': 1, 'Heat': 1}


User 1850
Movies Seen:
Grumpy Old Men, Twelve Monkeys, Toy story, Jumanji, Ace Ventura: When Nature Calls, Shichinin no samurai, Pocahontas, Father of the Bride Part II, The American President, Casino, Mortal Kombat

Possible Recommendations:
Twelve Monkeys, Shichinin no samurai, Toy story, Jumanji --> Babe (supp: 0.15, conf: 0.69)
Twelve Monkeys, Shichinin no samurai, Toy story, Jumanji --> GoldenEye (supp: 0.15, conf: 0.70)
Twelve Monkeys, Shichinin no samurai, Toy story --> Babe (supp: 0.22, conf: 0.59)
Twelve Monkeys, Shichinin no samurai, Jumanji --> Babe (supp: 0.16, conf: 0.65)
Twelve Monkeys, Toy story, Jumanji --> Babe (supp: 0.17, conf: 0.68)
Shichinin no samurai, Toy story, Jumanji --> Babe (supp: 0.18, conf: 0.68)
Twelve Monkeys, Toy story, Jumanji --> GoldenEye 

Twelve Monkeys, Babe, Jumanji --> Toy story (supp: 0.17, conf: 0.93)
Twelve Monkeys, Shichinin no samurai, Jumanji --> Toy story (supp: 0.22, conf: 0.88)
Babe, Shichinin no samurai, Jumanji --> Toy story (supp: 0.18, conf: 0.93)
Twelve Monkeys, Shichinin no samurai, Jumanji --> GoldenEye (supp: 0.17, conf: 0.67)
Twelve Monkeys, Babe, Shichinin no samurai --> GoldenEye (supp: 0.16, conf: 0.66)
Twelve Monkeys, Shichinin no samurai, Jumanji --> Ace Ventura: When Nature Calls (supp: 0.17, conf: 0.66)
Twelve Monkeys, Clueless, Shichinin no samurai --> Toy story (supp: 0.19, conf: 0.88)
Clueless, Shichinin no samurai, Jumanji --> Toy story (supp: 0.15, conf: 0.92)
Babe, Clueless, Shichinin no samurai --> Toy story (supp: 0.15, conf: 0.93)
Get Shorty, Shichinin no samurai, Twelve Monkeys --> Toy story (supp: 0.16, conf: 0.85)
Twelve Monkeys, Shichinin no samurai --> Toy story (supp: 0.37, conf: 0.77)
Twelve Monkeys, Babe --> Toy story (supp: 0.25, conf: 0.89)
Babe, Shichinin no samurai --> To

Twelve Monkeys, Toy story --> Casino (supp: 0.18, conf: 0.40)
Twelve Monkeys, Shichinin no samurai --> Casino (supp: 0.20, conf: 0.42)
Shichinin no samurai, Toy story --> Casino (supp: 0.19, conf: 0.41)
Twelve Monkeys, Toy story --> Get Shorty (supp: 0.18, conf: 0.41)
Twelve Monkeys --> Jumanji (supp: 0.29, conf: 0.48)
Babe --> Jumanji (supp: 0.24, conf: 0.60)
Shichinin no samurai --> Jumanji (supp: 0.30, conf: 0.48)
Toy story --> Jumanji (supp: 0.34, conf: 0.51)
Twelve Monkeys --> GoldenEye (supp: 0.29, conf: 0.48)
Toy story --> GoldenEye (supp: 0.31, conf: 0.48)
Babe --> GoldenEye (supp: 0.23, conf: 0.57)
Shichinin no samurai --> GoldenEye (supp: 0.30, conf: 0.48)
Ace Ventura: When Nature Calls --> Jumanji (supp: 0.25, conf: 0.66)
Ace Ventura: When Nature Calls --> GoldenEye (supp: 0.22, conf: 0.58)
Twelve Monkeys --> Clueless (supp: 0.25, conf: 0.41)
Toy story --> Clueless (supp: 0.28, conf: 0.43)
Ace Ventura: When Nature Calls --> Clueless (supp: 0.19, conf: 0.51)
Babe --> Clueless

Toy story --> GoldenEye (supp: 0.31, conf: 0.48)
Toy story --> Ace Ventura: When Nature Calls (supp: 0.30, conf: 0.45)
Toy story --> Clueless (supp: 0.28, conf: 0.43)

Frequency of Recommendations:
{'Shichinin no samurai': 1, 'Twelve Monkeys': 1, 'Babe': 1, 'Jumanji': 1, 'GoldenEye': 1, 'Ace Ventura: When Nature Calls': 1, 'Clueless': 1}


User 1906
Movies Seen:
Twelve Monkeys, Toy story, Jumanji, GoldenEye, Ace Ventura: When Nature Calls, Get Shorty, Clueless, Heat, Dead Man Walking, Father of the Bride Part II, Dangerous Minds, Cutthroat Island

Possible Recommendations:
Twelve Monkeys, Toy story, Jumanji, GoldenEye --> Shichinin no samurai (supp: 0.15, conf: 0.92)
Ace Ventura: When Nature Calls, Twelve Monkeys, Toy story, Jumanji --> Shichinin no samurai (supp: 0.15, conf: 0.90)
Twelve Monkeys, Toy story, Jumanji --> Babe (supp: 0.17, conf: 0.68)
Twelve Monkeys, Toy story, Jumanji --> Shichinin no samurai (supp: 0.22, conf: 0.88)
Twelve Monkeys, Toy story, GoldenEye --> Babe (supp: 